In [20]:
from IPython.display import HTML

## Testing recognition from bash

In [ ]:
!python mmaction2/demo/demo_skeleton.py data/uji_jalan.mp4 data/uji_jalan_out.mp4 \
    --config mmaction2/configs/skeleton/posec3d/slowonly_r50_8xb16-u48-240e_ntu60-xsub-keypoint.py \
    --checkpoint https://download.openmmlab.com/mmaction/skeleton/posec3d/slowonly_r50_u48_240e_ntu60_xsub_keypoint/slowonly_r50_u48_240e_ntu60_xsub_keypoint-f3adabf1.pth \
    --det-config mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py \
    --det-checkpoint http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth \
    --det-score-thr 0.9 \
    --det-cat-id 0 \
    --pose-config mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py \
    --pose-checkpoint https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth \
    --label-map mmaction2/tools/data/skeleton/label_map_ntu60.txt

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan.mp4"></video>')

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan_out.mp4"></video>')

## Testing from python

In [11]:
import tempfile

import cv2
import mmcv
import mmengine
import torch
from mmengine.utils import track_iter_progress

from mmaction.apis import (detection_inference, inference_skeleton,
                           init_recognizer, pose_inference)
from mmaction.registry import VISUALIZERS
from mmaction.utils import frame_extract

import moviepy.editor as mpy

In [3]:
FONTFACE = cv2.FONT_HERSHEY_DUPLEX
FONTSCALE = 0.75
FONTCOLOR = (255, 255, 255)  # BGR, white
THICKNESS = 1
LINETYPE = 1

def visualize(pose_config, out_filename, frames, data_samples, action_label):
    pose_config = mmengine.Config.fromfile(pose_config)
    visualizer = VISUALIZERS.build(pose_config.visualizer)
    visualizer.set_dataset_meta(data_samples[0].dataset_meta)

    vis_frames = []
    print('Drawing skeleton for each frame')
    for d, f in track_iter_progress(list(zip(data_samples, frames))):
        f = mmcv.imconvert(f, 'bgr', 'rgb')
        visualizer.add_datasample(
            'result',
            f,
            data_sample=d,
            draw_gt=False,
            draw_heatmap=False,
            draw_bbox=True,
            show=False,
            wait_time=0,
            out_file=None,
            kpt_thr=0.3)
        vis_frame = visualizer.get_image()
        cv2.putText(vis_frame, action_label, (10, 30), FONTFACE, FONTSCALE,
                    FONTCOLOR, THICKNESS, LINETYPE)
        vis_frames.append(vis_frame)

    vid = mpy.ImageSequenceClip(vis_frames, fps=24)
    vid.write_videofile(out_filename, remove_temp=True)

In [4]:
video = 'data/uji_jalan.mp4'
out_filename = 'data/uji_jalan_out.mp4'

# Choose to use an action classification config
config = 'mmaction2/configs/skeleton/posec3d/slowonly_r50_8xb16-u48-240e_ntu60-xsub-keypoint.py'
# Setup a checkpoint file to load
checkpoint = 'https://download.openmmlab.com/mmaction/skeleton/posec3d/slowonly_r50_u48_240e_ntu60_xsub_keypoint/slowonly_r50_u48_240e_ntu60_xsub_keypoint-f3adabf1.pth'

# human detection config
det_config = 'mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py'
det_checkpoint = 'http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth'
det_score_thr = 0.9
det_cat_id = 0

# pose estimation config
pose_config = 'mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py'
pose_checkpoint = 'https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth'
label_map = 'mmaction2/tools/data/skeleton/label_map_ntu60.txt'

In [5]:
device = 'cuda:0'
short_side = 480

In [6]:
tmp_dir = tempfile.TemporaryDirectory()
frame_paths, frames = frame_extract(video, short_side,
                                    tmp_dir.name)

h, w, _ = frames[0].shape

In [7]:
frames

[array([[[192, 179, 154],
         [192, 179, 154],
         [193, 180, 155],
         ...,
         [198, 182, 160],
         [198, 182, 160],
         [198, 182, 160]],
 
        [[192, 179, 154],
         [192, 179, 154],
         [193, 180, 155],
         ...,
         [198, 182, 160],
         [198, 182, 160],
         [198, 182, 160]],
 
        [[192, 179, 154],
         [192, 179, 154],
         [193, 180, 155],
         ...,
         [196, 182, 160],
         [196, 182, 160],
         [195, 181, 159]],
 
        ...,
 
        [[180, 159, 126],
         [180, 158, 128],
         [180, 157, 129],
         ...,
         [ 48,  30,  20],
         [ 46,  28,  18],
         [ 43,  25,  15]],
 
        [[175, 156, 116],
         [177, 157, 120],
         [179, 158, 123],
         ...,
         [ 54,  34,  24],
         [ 55,  35,  25],
         [ 51,  31,  21]],
 
        [[171, 154, 109],
         [174, 156, 114],
         [180, 161, 121],
         ...,
         [ 54,  34,  24],
  

In [10]:
frame_paths

['/tmp/tmpjkoayg7a/uji_jalan/img_000001.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000002.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000003.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000004.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000005.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000006.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000007.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000008.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000009.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000010.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000011.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000012.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000013.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000014.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000015.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000016.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000017.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000018.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000019.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000020.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_000021.jpg',
 '/tmp/tmpjkoayg7a/uji_jalan/img_0

In [8]:
# Get Human detection results.
det_results, _ = detection_inference(det_config, det_checkpoint,
                                     frame_paths, det_score_thr,
                                     det_cat_id, device)
torch.cuda.empty_cache()

Loads checkpoint by http backend from path: http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth
Performing Human Detection for each frame
[                                                  ] 0/319, elapsed: 0s, ETA:02/19 12:40:19 - mmengine - WARNING - "FileClient" will be deprecated in future. Please use io functions in https://mmengine.readthedocs.io/en/latest/api/fileio.html#file-io
02/19 12:40:19 - mmengine - WARNING - "HardDiskBackend" is the alias of "LocalBackend" and the former will be deprecated in future.
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 319/319, 24.9 task/s, elapsed: 13s, ETA:     0s


In [9]:
det_results

[array([[509.4602  ,  96.892715, 641.25543 , 474.8942  ]], dtype=float32),
 array([[504.92947,  90.40763, 637.85297, 472.22046]], dtype=float32),
 array([[508.7126 ,  91.79281, 633.26965, 474.41754]], dtype=float32),
 array([[511.9911 ,  86.06832, 636.19403, 473.42233]], dtype=float32),
 array([[505.19684,  93.12396, 632.2881 , 471.82343]], dtype=float32),
 array([[507.10352 ,  91.331505, 628.57245 , 476.43365 ]], dtype=float32),
 array([[503.74918,  93.41931, 623.3195 , 475.6536 ]], dtype=float32),
 array([[504.9984 ,  93.25105, 616.6103 , 475.34705]], dtype=float32),
 array([[504.3372 ,  91.869  , 603.50446, 475.43787]], dtype=float32),
 array([[493.44376,  91.8932 , 595.3956 , 474.30212]], dtype=float32),
 array([[490.29193,  95.32662, 585.8031 , 469.82367]], dtype=float32),
 array([[489.57776,  95.73166, 580.05164, 472.82388]], dtype=float32),
 array([[489.6901 ,  98.37758, 577.7878 , 473.12323]], dtype=float32),
 array([[461.24942,  97.82076, 571.359  , 475.476  ]], dtype=float32)

In [20]:
# Get Pose estimation results.
pose_results, pose_data_samples = pose_inference(pose_config,
                                                 pose_checkpoint,
                                                 frame_paths, det_results,
                                                 device)
torch.cuda.empty_cache()

02/16 12:59:07 - mmengine - WARNING - The current default scope "mmdet" is not "mmpose", `init_default_scope` will force set the currentdefault scope to "mmpose".
Loads checkpoint by http backend from path: https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth
Performing Human Pose Estimation for each frame
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 319/319, 13.6 task/s, elapsed: 23s, ETA:     0s


In [21]:
pose_data_samples

[<PoseDataSample(
 
     META INFORMATION
     pad_shape: (256, 192)
     input_center: array([575.3578 , 285.89346], dtype=float32)
     input_scale: array([354.37637, 472.50183], dtype=float32)
     input_size: (192, 256)
     batch_input_shape: (256, 192)
     dataset_name: 'coco'
     img_path: '/tmp/tmpq0ad4nnj/uji_jalan/img_000001.jpg'
     flip_indices: [0, 2, 1, 4, 3, 6, 5, 8, 7, 10, 9, 12, 11, 14, 13, 16, 15]
     ori_shape: (480, 853)
     img_shape: (480, 853)
 
     DATA FIELDS
     dataset_meta: 
         dataset_name: 'coco'
         num_keypoints: 17
         keypoint_id2name: 
             0: 'nose'
             1: 'left_eye'
             2: 'right_eye'
             3: 'left_ear'
             4: 'right_ear'
             5: 'left_shoulder'
             6: 'right_shoulder'
             7: 'left_elbow'
             8: 'right_elbow'
             9: 'left_wrist'
             10: 'right_wrist'
             11: 'left_hip'
             12: 'right_hip'
             13: 'left_kne

In [22]:
# Initialize the recognizer
config = mmengine.Config.fromfile(config)
# build the model from a config file and a checkpoint file
model = init_recognizer(config, checkpoint, device)

# Get Action classification results.
result = inference_skeleton(model, pose_results, (h, w))

02/16 12:59:32 - mmengine - WARNING - The current default scope "mmpose" is not "mmaction", `init_default_scope` will force set the currentdefault scope to "mmaction".
Loads checkpoint by http backend from path: https://download.openmmlab.com/mmaction/skeleton/posec3d/slowonly_r50_u48_240e_ntu60_xsub_keypoint/slowonly_r50_u48_240e_ntu60_xsub_keypoint-f3adabf1.pth


In [23]:
# find the index of highest predicted score on result
max_pred_index = result.pred_score.argmax().item()

label_map = [x.strip() for x in open(label_map).readlines()]

# set the highest predicted label as action_label
action_label = label_map[max_pred_index]
print(action_label)

staggering


In [24]:
visualize(pose_config, out_filename, frames, pose_data_samples, action_label)

Drawing skeleton for each frame
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 319/319, 675.7 task/s, elapsed: 0s, ETA:     0s
Moviepy - Building video data/uji_jalan_out.mp4.
Moviepy - Writing video data/uji_jalan_out.mp4



Moviepy - Done !
Moviepy - video ready data/uji_jalan_out.mp4


In [25]:
tmp_dir.cleanup()

In [27]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan.mp4"></video>')

In [28]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan_out.mp4"></video>')

##TESTING MANDA

In [ ]:
!python mmaction2/demo/demo_skeleton.py data/uji_duduk_drone_25.mp4 data/uji_duduk_drone_25_out.mp4 \
    --config mmaction2/configs/skeleton/posec3d/slowonly_r50_u48_240e_ntu120_xsub_keypoint.py \
    --checkpoint work_dirs/slowonly_r50_u48_240e_ntu120_xsub_keypoint/best_top1_acc_epoch_90_8.pth \
    --det-config mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py \
    --det-checkpoint http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth \
    --det-score-thr 0.9 \
    --det-cat-id 0 \
    --pose-config mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py \
    --pose-checkpoint https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth \
    --label-map mmaction2/tools/data/skeleton/label_5.txt

##MANIPULASI

In [12]:
def visualize(pose_config, out_filename, frames, data_samples, action_label):
    pose_config = mmengine.Config.fromfile(pose_config)
    visualizer = VISUALIZERS.build(pose_config.visualizer)
    visualizer.set_dataset_meta(data_samples[0].dataset_meta)

    vis_frames = []
    print('Drawing skeleton for each frame')
    for d, f in track_iter_progress(list(zip(data_samples, frames))):
        f = mmcv.imconvert(f, 'bgr', 'rgb')
        visualizer.add_datasample(
            'result',
            f,
            data_sample=d,
            draw_gt=False,
            draw_heatmap=False,
            draw_bbox=True,
            show=False,
            wait_time=0,
            out_file=None,
            kpt_thr=0.3)
        vis_frame = visualizer.get_image()
        cv2.putText(vis_frame, action_label, (10, 30), FONTFACE, FONTSCALE,
                    FONTCOLOR, THICKNESS, LINETYPE)
        vis_frames.append(vis_frame)

    vid = mpy.ImageSequenceClip(vis_frames, fps=24)
    vid.write_videofile(out_filename, remove_temp=True)

In [13]:
FONTFACE = cv2.FONT_HERSHEY_DUPLEX
FONTSCALE = 0.75
FONTCOLOR = (255, 255, 255)  # BGR, white
THICKNESS = 1
LINETYPE = 1

In [28]:
video = 'data/dji_fly_20240216_153006_10_1708074336344_video_30.mp4'
out_filename = 'data/drone_bbox_2orang.mp4'

# Choose to use an action classification config
config = 'mmaction2/configs/skeleton/posec3d/slowonly_r50_8xb16-u48-240e_ntu60-xsub-keypoint.py'
# Setup a checkpoint file to load
checkpoint = 'https://download.openmmlab.com/mmaction/skeleton/posec3d/slowonly_r50_u48_240e_ntu60_xsub_keypoint/slowonly_r50_u48_240e_ntu60_xsub_keypoint-f3adabf1.pth'

# human detection config
det_config = 'mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py'
det_checkpoint = 'http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth'
det_score_thr = 0.9
det_cat_id = 0

# pose estimation config
pose_config = 'mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py'
pose_checkpoint = 'https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth'
label_map = 'mmaction2/tools/data/skeleton/label_map_ntu60.txt'

In [29]:
device = 'cuda:0'
short_side = 480

In [30]:
tmp_dir = tempfile.TemporaryDirectory()
frame_paths, frames = frame_extract(video, short_side,
                                    tmp_dir.name)

h, w, _ = frames[0].shape

In [31]:
# Get Human detection results.
det_results, _ = detection_inference(det_config, det_checkpoint,
                                     frame_paths, det_score_thr,
                                     det_cat_id, device)
torch.cuda.empty_cache()

Loads checkpoint by http backend from path: http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth
Performing Human Detection for each frame
[>>>>>>>>>>>>>>>>>>>>>>>>>>] 8725/8725, 21.2 task/s, elapsed: 412s, ETA:     0s


In [34]:
print(det_results)

[array([[177.36595 ,  61.680634, 314.83603 , 325.99332 ],
       [280.2932  ,  95.2305  , 411.57803 , 403.90833 ]], dtype=float32), array([[173.85674 ,  62.100506, 312.8996  , 325.85995 ],
       [277.37234 ,  95.42194 , 408.86752 , 402.43222 ]], dtype=float32), array([[178.7161 ,  61.83453, 313.92694, 325.848  ],
       [278.77383,  96.1548 , 405.46625, 406.89975]], dtype=float32), array([[179.16031,  61.0928 , 312.80795, 327.02444],
       [270.0288 ,  97.52948, 394.46906, 405.63535]], dtype=float32), array([[179.72713 ,  62.562744, 308.82785 , 326.82968 ],
       [266.7981  ,  99.15068 , 385.94708 , 406.51007 ]], dtype=float32), array([[180.97443,  63.97111, 306.14087, 325.00598],
       [265.02905,  99.32489, 380.9161 , 403.48618]], dtype=float32), array([[253.47977 ,  93.245544, 369.7485  , 405.24478 ],
       [179.19437 ,  65.76177 , 302.10886 , 323.23904 ]], dtype=float32), array([[250.45303 ,  90.774155, 362.95755 , 406.7267  ],
       [180.6892  ,  66.78095 , 297.48117 , 320.9

In [22]:
detection_inference(det_config, det_checkpoint,
                                     frame_paths, det_score_thr,
                                     det_cat_id, device)

Loads checkpoint by http backend from path: http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth
Performing Human Detection for each frame
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 555/555, 25.4 task/s, elapsed: 22s, ETA:     0s


([array([[685.2418 , 184.37494, 804.9909 , 371.71255]], dtype=float32),
  array([[683.43854, 184.83844, 801.1636 , 373.57355]], dtype=float32),
  array([[684.3535 , 184.77835, 797.584  , 371.95416]], dtype=float32),
  array([[684.5196 , 185.43842, 796.54425, 374.23398]], dtype=float32),
  array([[684.32196, 185.25223, 792.8482 , 374.066  ]], dtype=float32),
  array([[685.7469 , 185.99214, 792.505  , 374.49023]], dtype=float32),
  array([[685.10614, 185.98196, 792.2925 , 374.65155]], dtype=float32),
  array([[683.7472 , 185.61339, 788.8749 , 374.89236]], dtype=float32),
  array([[684.42426, 185.61409, 787.03265, 374.13297]], dtype=float32),
  array([[684.0488 , 184.56732, 783.4877 , 373.82983]], dtype=float32),
  array([[683.93146, 185.00508, 782.3626 , 374.48938]], dtype=float32),
  array([[684.565  , 185.35402, 780.1933 , 374.16266]], dtype=float32),
  array([[684.4983 , 184.65701, 779.3094 , 375.02054]], dtype=float32),
  array([[685.86084, 184.59856, 777.58325, 374.3294 ]], dtype=fl

In [ ]:
# Get Pose estimation results.
pose_results, pose_data_samples = pose_inference(pose_config,
                                                 pose_checkpoint,
                                                 frame_paths, det_results,
                                                 device)
torch.cuda.empty_cache()

In [ ]:
visualize(pose_config, out_filename, frames, pose_data_samples, "pistol")

tmp_dir.cleanup()

In [21]:
HTML('<video width=50% controls autoplay loop><source src="/home/ciis-compnew/Desktop/ciis_dataset/dji_fly_20230316_160706_6_1678961605643_video.mp4"></video>')

## Testing recognition + detection from bash

In [1]:
!python mmaction2/demo/demo_video_structuralize.py \
    --video mmaction2/demo/test_video_structuralize.mp4 \
    --out-filename mmaction2/demo/test_stdet_recognition_output.mp4 \
\
    --rgb-stdet-config mmaction2/configs/detection/slowonly/slowonly_kinetics400-pretrained-r101_8xb16-8x8x1-20e_ava21-rgb.py \
    --skeleton-stdet-checkpoint https://download.openmmlab.com/mmaction/skeleton/posec3d/posec3d_ava.pth \
\
    --det-config mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py \
    --det-checkpoint http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth \
\
    --pose-config mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py \
    --pose-checkpoint https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth \
\
    --skeleton-config mmaction2/configs/skeleton/posec3d/slowonly_r50_8xb16-u48-240e_ntu60-xsub-keypoint.py \
    --skeleton-checkpoint https://download.openmmlab.com/mmaction/skeleton/posec3d/posec3d_k400.pth \
\
    --use-skeleton-stdet \
    --use-skeleton-recog \
\
    --label-map-stdet mmaction2/tools/data/ava/label_map.txt \
    --label-map mmaction2/tools/data/kinetics/label_map_k400.txt

Loads checkpoint by http backend from path: http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth
Performing Human Detection for each frame
[                                                  ] 0/300, elapsed: 0s, ETA:02/19 12:22:07 - mmengine - WARNING - "FileClient" will be deprecated in future. Please use io functions in https://mmengine.readthedocs.io/en/latest/api/fileio.html#file-io
02/19 12:22:07 - mmengine - WARNING - "HardDiskBackend" is the alias of "LocalBackend" and the former will be deprecated in future.
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 300/300, 17.2 task/s, elapsed: 17s, ETA:     0s
Loads checkpoint by http backend from path: https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth
Performing Human Pose Estimation for each frame
[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 300/300, 17.0 task/s, elapsed: 18s, ETA:     0s
Use skeleton-based rec

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan.mp4"></video>')

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="data/uji_jalan_vs_out.mp4"></video>')

In [ ]:
!python mmaction2/demo/demo_video_structuralize.py \
    --video mmaction2/demo/demo_skeleton.mp4 \
    --out-filename mmaction2/demo/demo_skeleton_vs_out.mp4 \
    --rgb-stdet-config mmaction2/configs/detection/slowonly/slowonly_kinetics400-pretrained-r101_8xb16-8x8x1-20e_ava21-rgb.py \
    --skeleton-stdet-checkpoint https://download.openmmlab.com/mmaction/skeleton/posec3d/posec3d_ava.pth \
    --det-config mmaction2/demo/demo_configs/faster-rcnn_r50_fpn_2x_coco_infer.py \
    --det-checkpoint http://download.openmmlab.com/mmdetection/v2.0/faster_rcnn/faster_rcnn_r50_fpn_2x_coco/faster_rcnn_r50_fpn_2x_coco_bbox_mAP-0.384_20200504_210434-a5d8aa15.pth \
    --pose-config mmaction2/demo/demo_configs/td-hm_hrnet-w32_8xb64-210e_coco-256x192_infer.py \
    --pose-checkpoint https://download.openmmlab.com/mmpose/top_down/hrnet/hrnet_w32_coco_256x192-c78dce93_20200708.pth \
    --skeleton-config mmaction2/configs/skeleton/posec3d/slowonly_r50_8xb16-u48-240e_ntu60-xsub-keypoint.py \
    --skeleton-checkpoint https://download.openmmlab.com/mmaction/skeleton/posec3d/posec3d_k400.pth \
    --use-skeleton-stdet \
    --use-skeleton-recog \
    --label-map-stdet mmaction2/tools/data/ava/label_map.txt \
    --label-map mmaction2/tools/data/kinetics/label_map_k400.txt

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="mmaction2/demo/demo_skeleton.mp4"></video>')

In [ ]:
HTML('<video width=50% controls autoplay loop><source src="mmaction2/demo/demo_skeleton_vs_out.mp4"></video>')